В качестве набора данных я выбрала датасет, демонстрирующий качество вина по содержанию в нем разных веществ (https://www.kaggle.com/uciml/red-wine-quality-cortez-et-al-2009/version/2).

Эта задача будет полезна в различных ресторанах, алкогольных магазинах, а также на различных винодельнях.

Датасет состоит пока что из одного файла, но для обучения модели я разобью его на 3 части.

В моем датасете хранятся следующие данные:

1)fixed acidit - фиксированная кислотность

2)volatile acidity - летучая кислотность

3)citric acid - лимонная кислота

4)residual sugar - остаточный сахар

5)chlorides - хлориды

6)free sulfur dioxide - свободный диоксид серы

7)total sulfur dioxide - общий диоксид серы

8)density - плотность

9)pH - водородный показатель

10)sulphates - сульфаты

11)alcohol - алкоголь

12)quality - качество - целевой признак - оценка вина от 0 до 10 баллов (на деле от 3 до 8)

Более подробное описание этого датасета по ссылке.

In [0]:
#Импорт библиотек 
from google.colab import drive
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.neighbors import KNeighborsRegressor, KNeighborsClassifier
from sklearn.metrics import accuracy_score, balanced_accuracy_score
from sklearn.metrics import precision_score, recall_score
from sklearn.linear_model import SGDClassifier
from sklearn.svm import SVC
from sklearn.model_selection import KFold
from sklearn.model_selection import GridSearchCV
from sklearn.tree import DecisionTreeClassifier
import seaborn as sns
import matplotlib.pyplot as plt
%matplotlib inline 
sns.set(style="ticks")

In [2]:
#Монтирую гугл диск, чтобы взять оттуда датасет
drive.mount("/content/gdrive", force_remount=True)

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/gdrive


In [0]:
#Загружаю данные с гугл диска
data = pd.read_csv('/content/gdrive/My Drive/winequality-red.csv', sep=",")

In [4]:
data.head(5)

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   
3                 17.0                  60.0   0.9980  3.16       0.58   
4                 11.0                  34.0   0.9978  3.51       0.56   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5  
3      9.8        6  
4      9.4        5

Нулевых значений и категориалных признаков нет - > обрабатывать нечего. В прошлой лабе были выбраны признаки, у которых наибольший коэффициент корреляции. 

In [5]:
cols_x = ['fixed acidity', 'citric acid', 'sulphates', 'alcohol']   
# целевой признак
col_y = 'quality'
#разделение данных  на тестовую и обучающую выборки 
X_train, X_test, y_train, y_test = train_test_split(data[cols_x], data[col_y], test_size = 0.5, random_state = 11)
N_train, _ = X_train.shape 
N_test,  _ = X_test.shape 
print (N_train, N_test)

799 800


#Обучение с помощью линейной модели 

In [6]:
grad = SGDClassifier().fit(X_train, y_train)


/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in SGDClassifier in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)


In [0]:
target_grad = grad.predict(X_test)

## Оценка качества линейной модели

In [0]:
def convert_target_to_binary(array:np.ndarray, target:int) -> np.ndarray:
    # Если целевой признак совпадает с указанным, то 1 иначе 0
    res = [1 if x==target else 0 for x in array]
    return res

In [9]:
# Если целевой признак == 6, 
# то будем считать этот случай 1 в бинарном признаке
bin_y_test = convert_target_to_binary(y_test, 6)
list(zip(y_test, bin_y_test))[0:15]

[(5, 0),
 (5, 0),
 (5, 0),
 (6, 1),
 (6, 1),
 (5, 0),
 (7, 0),
 (5, 0),
 (5, 0),
 (6, 1),
 (5, 0),
 (6, 1),
 (5, 0),
 (3, 0),
 (6, 1)]

In [0]:
# Конвертация предсказанных признаков
bin_target_grad = convert_target_to_binary(target_grad, 6)

In [11]:
ac_grad = accuracy_score(y_test, target_grad)
bas_grad = balanced_accuracy_score(bin_y_test, bin_target_grad)
rec_grad = recall_score(bin_y_test, bin_target_grad)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_grad, bas_grad, rec_grad))

accuracy_score: 0.02375
balanced_accuracy_score: 0.5
recall_score: 0.0


# Обучение с помощью SVM

In [0]:
svmcl = SVC(kernel='rbf', gamma=0.5, C=1.0).fit(X_train, y_train)

In [0]:
target_svm = svmcl.predict(X_test)

## Оценка качества метода опорных векторов 

In [0]:
# Конвертация предсказанных признаков
bin_target_svm = convert_target_to_binary(target_svm, 6)

In [16]:
ac_svm = accuracy_score(y_test, target_svm)
bas_svm = balanced_accuracy_score(bin_y_test, bin_target_svm)
rec_svm = recall_score(bin_y_test, bin_target_svm)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_svm, bas_svm, rec_svm))

accuracy_score: 0.5725
balanced_accuracy_score: 0.6011622789987316
recall_score: 0.5398773006134969


# Обучение с помощью деревьев принятия решений

In [0]:
dtcl = DecisionTreeClassifier(random_state=1, max_depth = 20).fit(X_train, y_train)

In [0]:
target_dtc = dtcl.predict(X_test)

##Оценка качества классификации методом деревьев принятия решений

In [0]:
# Конвертация предсказанных признаков
bin_target_dtc = convert_target_to_binary(target_dtc, 6)

In [55]:
ac_dtc = accuracy_score(y_test, target_dtc)
bas_dtc = balanced_accuracy_score(bin_y_test, bin_target_dtc)
rec_dtc = recall_score(bin_y_test, bin_target_dtc)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_dtc, bas_dtc, rec_dtc))

accuracy_score: 0.54
balanced_accuracy_score: 0.6077826098211281
recall_score: 0.5214723926380368


#Подбор гиперпараметра с использованием GridSearchCV и кросс-валидации 

## Для градиентного спуска

In [39]:
n_range = np.array(np.arange(0.0001,1,0.05))
tuned_parameters = [{'alpha': n_range}]
tuned_parameters

[{'alpha': array([1.000e-04, 5.010e-02, 1.001e-01, 1.501e-01, 2.001e-01, 2.501e-01,
         3.001e-01, 3.501e-01, 4.001e-01, 4.501e-01, 5.001e-01, 5.501e-01,
         6.001e-01, 6.501e-01, 7.001e-01, 7.501e-01, 8.001e-01, 8.501e-01,
         9.001e-01, 9.501e-01])}]

In [0]:
grad_gs = GridSearchCV(SGDClassifier(), tuned_parameters, cv=KFold(n_splits=10), scoring='accuracy')
grad_gs.fit(data[cols_x], data[col_y])

In [28]:
grad_gs.best_params_

{'alpha': 0.0601}

##Обучение с подобранным параметром

In [29]:
grad_gs.best_estimator_.fit(X_train, y_train)
target_grad_gs = grad_gs.best_estimator_.predict(X_test)

/usr/local/lib/python3.6/dist-packages/sklearn/linear_model/stochastic_gradient.py:166: FutureWarning: max_iter and tol parameters have been added in SGDClassifier in 0.19. If both are left unset, they default to max_iter=5 and tol=None. If tol is not None, max_iter defaults to max_iter=1000. From 0.21, default max_iter will be 1000, and default tol will be 1e-3.
  FutureWarning)


### Проверка качества модели

In [0]:
# Конвертация предсказанных признаков
bin_target_grad_gs = convert_target_to_binary(target_grad_gs, 6)

In [31]:
#Новая модель
ac_grad_gs = accuracy_score(y_test, target_grad_gs)
bas_grad_gs = balanced_accuracy_score(bin_y_test, bin_target_grad_gs)
rec_grad_gs = recall_score(bin_y_test, bin_target_grad_gs)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_grad_gs, bas_grad_gs, rec_grad_gs))

accuracy_score: 0.42125
balanced_accuracy_score: 0.5
recall_score: 0.0


In [32]:
#Старая модель
ac_grad = accuracy_score(y_test, target_grad)
bas_grad = balanced_accuracy_score(bin_y_test, bin_target_grad)
rec_grad = recall_score(bin_y_test, bin_target_grad)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_grad, bas_grad, rec_grad))

accuracy_score: 0.02375
balanced_accuracy_score: 0.5
recall_score: 0.0


## Для SVM

In [0]:
tuned_parameters_svm = [{'gamma': n_range}]

In [41]:
svm_gs = GridSearchCV(SVC(), tuned_parameters_svm, cv=KFold(n_splits=5), scoring='accuracy')
svm_gs.fit(data[cols_x], data[col_y])

GridSearchCV(cv=KFold(n_splits=5, random_state=None, shuffle=False),
       error_score='raise-deprecating',
       estimator=SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto_deprecated',
  kernel='rbf', max_iter=-1, probability=False, random_state=None,
  shrinking=True, tol=0.001, verbose=False),
       fit_params=None, iid='warn', n_jobs=None,
       param_grid=[{'gamma': array([1.000e-04, 5.010e-02, 1.001e-01, 1.501e-01, 2.001e-01, 2.501e-01,
       3.001e-01, 3.501e-01, 4.001e-01, 4.501e-01, 5.001e-01, 5.501e-01,
       6.001e-01, 6.501e-01, 7.001e-01, 7.501e-01, 8.001e-01, 8.501e-01,
       9.001e-01, 9.501e-01])}],
       pre_dispatch='2*n_jobs', refit=True, return_train_score='warn',
       scoring='accuracy', verbose=0)

In [42]:
svm_gs.best_params_

{'gamma': 0.050100000000000006}

##Обучение с подобранным параметром

In [0]:
svm_gs.best_estimator_.fit(X_train, y_train)
target_svm_gs = svm_gs.best_estimator_.predict(X_test)

### Проверка качества модели

In [0]:
# Конвертация предсказанных признаков
bin_target_svm_gs = convert_target_to_binary(target_svm_gs, 6)

In [45]:
#Новая модель
ac_svm_gs = accuracy_score(y_test, target_svm_gs)
bas_svm_gs = balanced_accuracy_score(bin_y_test, bin_target_svm_gs)
rec_svm_gs = recall_score(bin_y_test, bin_target_svm_gs)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_svm_gs, bas_svm_gs, rec_svm_gs))

accuracy_score: 0.5725
balanced_accuracy_score: 0.6045080375863944
recall_score: 0.5950920245398773


In [46]:
#Старая модель
ac_svm = accuracy_score(y_test, target_svm)
bas_svm = balanced_accuracy_score(bin_y_test, bin_target_svm)
rec_svm = recall_score(bin_y_test, bin_target_svm)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_svm, bas_svm, rec_svm))

accuracy_score: 0.5725
balanced_accuracy_score: 0.6011622789987316
recall_score: 0.5398773006134969


##Для деревьев принятия решений

In [48]:
n_range_dtc = np.array(range(1,1000,30))
tuned_parameters_dtc = [{'max_depth': n_range_dtc}]
tuned_parameters_dtc

[{'max_depth': array([  1,  31,  61,  91, 121, 151, 181, 211, 241, 271, 301, 331, 361,
         391, 421, 451, 481, 511, 541, 571, 601, 631, 661, 691, 721, 751,
         781, 811, 841, 871, 901, 931, 961, 991])}]

In [0]:
dtc_gs = GridSearchCV(DecisionTreeClassifier(), tuned_parameters_dtc, cv=KFold(n_splits=10), scoring= 'precision_weighted')
dtc_gs.fit(data[cols_x], data[col_y])

In [65]:
dtc_gs.best_params_

{'max_depth': 781}

##Обучение с подобранным параметром

In [0]:
dtc_gs.best_estimator_.fit(X_train, y_train)
target_dtc_gs = dtc_gs.best_estimator_.predict(X_test)

### Проверка качества модели

In [0]:
# Конвертация предсказанных признаков
bin_target_dtc_gs = convert_target_to_binary(target_dtc_gs, 6)

In [68]:
#Новая модель
ac_dtc_gs = accuracy_score(y_test, target_dtc_gs)
bas_dtc_gs = balanced_accuracy_score(bin_y_test, bin_target_dtc_gs)
rec_dtc_gs = recall_score(bin_y_test, bin_target_dtc_gs)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_dtc_gs, bas_dtc_gs, rec_dtc_gs))

accuracy_score: 0.54625
balanced_accuracy_score: 0.6256180269731563
recall_score: 0.5276073619631901


In [69]:
#Старая модель
ac_dtc = accuracy_score(y_test, target_dtc)
bas_dtc = balanced_accuracy_score(bin_y_test, bin_target_dtc)
rec_dtc = recall_score(bin_y_test, bin_target_dtc)
print('''accuracy_score: {0}
balanced_accuracy_score: {1}
recall_score: {2}'''.format(ac_dtc, bas_dtc, rec_dtc))

accuracy_score: 0.54
balanced_accuracy_score: 0.6077826098211281
recall_score: 0.5214723926380368


In [0]:
from sklearn.externals.six import StringIO  
from IPython.display import Image  
from sklearn.tree import export_graphviz
import pydotplus

In [0]:
dot_data = StringIO()

In [0]:
export_graphviz(dtcl, out_file=dot_data,  
                filled=True, rounded=True,
                special_characters=True)

In [73]:
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())